In [1]:
import pandas as pd
import numpy as np
import talib as talib
from pyecharts import options as opts
from pyecharts.globals import *
from pyecharts.charts import *
import re
# from pyecharts.

from datetime import datetime,timedelta
import matplotlib.pyplot as plt

g_colors = [
    '#111111',
    '#f06020',
    '#1ac6bc',
    '#cc1b9e',
    '#bde01e',
    '#211ac6',
    '#f0bd20',
    '#791ac6',
    '#f0e620',
    '#e61f2e',
    '#38cb1b',
    '#74d3ff',
    '#ffb174',
    '#678ce3',
    '#ffcd74',
    '#8867e3',
    '#ffe974',
    '#cf67e3',
    '#b9ee6c',
    '#ff7f74',
    '#ed6ca1',
    '#67e384',
    '#ff7f74'
]


# %matplotlib inline
#正常显示画图时出现的中文和负号
from pylab import mpl
mpl.rcParams['font.sans-serif']=['SimHei']
mpl.rcParams['axes.unicode_minus']=False

#使用tushare获取交易数据
#设置token
import tushare as ts
#注意token更换为你在tushare网站上获取的
token='36d50a0386e9066b5c79c2de58ea2d3a9b980020041adc910f76bfc7'
ts.set_token(token)
pro=ts.pro_api()
index={'上证综指': '000001.SH',
        '深证成指': '399001.SZ',
        '沪深300': '000300.SH',
        '创业板指': '399006.SZ',
        '上证50': '000016.SH',
        '中证500': '000905.SH',
        '中小板指': '399005.SZ',
        '上证180': '000010.SH'}
#获取当前交易的股票代码和名称
def get_code():
    df = pro.stock_basic(exchange='', list_status='L')
    codes=df.ts_code.values
    names=df.name.values
    stock=dict(zip(names,codes))
    #合并指数和个股成一个字典
    stocks=dict(stock,**index)
    return stocks

def get_index_code():
    return index;

def get_code_df():
    df = pro.stock_basic(exchange='', list_status='L')
    return df

def get_ts_code (code_df, keyword ): 
    code =''
    if re.match( r'\d{6}', keyword):
        code_df.index = code_df['symbol']
    else:
        code_df.index = code_df['name']
    code=code_df.loc[keyword,'ts_code']
    symbol=code_df.loc[keyword,'symbol']
    name=code_df.loc[keyword,'name']
    return (code,symbol,name)

#获取行情数据
def get_daily_data(stock,start,end):
    #如果代码在字典index里，则取的是指数数据
    stock_info = {}
    if stock in get_index_code(): 
        code=get_index_code()[stock]
        df=pro.index_daily(ts_code=code,start_date=start, end_date=end)
        df.index=pd.to_datetime(df.trade_date)
        stock_info['name'] = stock
        stock_info['symbol'] = code
    #否则取的是个股数据
    else:
        code_df = get_code_df()
        code,stock_info['symbol'],stock_info['name'] = get_ts_code(code_df,stock)
        print("pro.daily ts_code"+code+start )
        df=ts.pro_bar(ts_code=code, adj='qfq', start_date=start, end_date=end)
#         df=pro.daily(ts_code=code,start_date=start, end_date=end)
#         df_adj = pro.adj_factor(ts_code=code, start_date=start,end_date=end)

        df.index=pd.to_datetime(df.trade_date)
#         df_adj.index=pd.to_datetime(df_adj.trade_date)
#         cur_adj = df_adj[ df.iloc[0].trade_date]['adj_factor'][0]
        
#         df['open']=df.loc[:,'open'] * df_adj['adj_factor'] / cur_adj
#         df['close']=df.loc[:,'close']* df_adj['adj_factor'] / cur_adj
#         df['high'] =df.loc[:,'high'] * df_adj['adj_factor'] / cur_adj
#         df['low'] =df.loc[:,'low'] * df_adj['adj_factor'] / cur_adj
#         df['amount'] =df.loc[:,'amount'] * df_adj['adj_factor'] / cur_adj
    #将交易日期设置为索引值

    df=df.sort_index()
    #计算收益率
    df['ret']=df.close/df.close.shift(1)-1
    return (df,stock_info)

def get_line(xdatas, data_dic):
    line= Line()
    line.add_xaxis(xaxis_data=xdatas)
    i = 0
    for key in data_dic:
        value = data_dic[key];
        line.add_yaxis(
            series_name=value['name'],
            y_axis=value['datas'],
            symbol="none",
            is_smooth=True,
            is_hover_animation=False,
            linestyle_opts=opts.LineStyleOpts(width=2, opacity=0.9),
            label_opts=opts.LabelOpts(is_show=False),
            itemstyle_opts=opts.ItemStyleOpts(color=g_colors[i]),
        )
        i+=1
        
    line.set_global_opts(xaxis_opts=opts.AxisOpts(type_="category"))
    return line

def get_kline (xdatas,kdatas,stock_info):
    c = (
        Kline(
                init_opts=opts.InitOpts(
            )
        )
        .add_xaxis(xaxis_data=xdatas)
        .add_yaxis(
            series_name='kline',
            y_axis=kdatas
        )
        .set_global_opts(
            title_opts=opts.TitleOpts(
                    title=stock_info['name'],
                    subtitle=stock_info['symbol'],
            ),
            xaxis_opts=opts.AxisOpts(
                        is_scale=True,
                        type_="category",
                        splitarea_opts=opts.SplitAreaOpts(
                        is_show=True, areastyle_opts=opts.AreaStyleOpts(opacity=1)
                    ),
            ),
            yaxis_opts=opts.AxisOpts(
                    is_scale=True,
                    splitarea_opts=opts.SplitAreaOpts(
                        is_show=True, areastyle_opts=opts.AreaStyleOpts(opacity=1)
                    ),
            ),
            legend_opts=opts.LegendOpts(
                is_show=False, pos_bottom=10, pos_left="center"
            ),
            datazoom_opts=[
                opts.DataZoomOpts(
                    is_show=True,
                    xaxis_index=[0,1,2],
                    type_="slider",
                    pos_top="90%",
                    range_start=90,
                    range_end=100,
                ),
#                 opts.DataZoomOpts(
#                     is_show=True,
#                     yaxis_index=[0],
#                     type_="slider",
#                     orient = 'vertical',
# #                     pos_top="90%",
#                     pos_right="0%",
#                     range_start=0,
#                     range_end=100,
#                 ),
            ],
            tooltip_opts=opts.TooltipOpts(
                    trigger="axis",
                    axis_pointer_type="cross",
                    background_color="rgba(245, 245, 245, 0.8)",
                    border_width=1,
                    border_color="#ccc",
                    textstyle_opts=opts.TextStyleOpts(color="#000"),
            ),
            visualmap_opts=opts.VisualMapOpts(
                    is_show=True,
                    dimension=2,
                    series_index=[5,6,7,8,9,10],
                    is_piecewise=True,
                    pieces=[
                        {"value": 1, "color": "#ff7f74"},
                        {"value": -1, "color": "#67e384"},
                    ],
                ),
                axispointer_opts=opts.AxisPointerOpts(
                    is_show=True,
                    link=[{"xAxisIndex": "all"}],
                    label=opts.LabelOpts(background_color="#777"),
                ),
                brush_opts=opts.BrushOpts(
                    x_axis_index="all",
                    brush_link="all",
                    out_of_brush={"colorAlpha": 0.1},
                    brush_type="lineX",
                ),
        )
    )
    return c


def get_volome(xdatas,vols,kdatas): 
    bar = (
        Bar(init_opts=opts.InitOpts())
        .add_xaxis(xaxis_data=xdatas)
        .add_yaxis(
            series_name="Volume",
            yaxis_data=[
                [i, vols[i], 1 if kdatas[i][0] > kdatas[i][1] else -1]
                for i in range(len(kdatas))
            ],
    #         yaxis_data = vols,
            xaxis_index=1,
            yaxis_index=1,
            label_opts=opts.LabelOpts(is_show=False)
        )
        .set_global_opts(
            xaxis_opts=opts.AxisOpts(
                type_="category",
                is_scale=True,
                grid_index=1,
                boundary_gap=False,
                axisline_opts=opts.AxisLineOpts(is_on_zero=False),
                axistick_opts=opts.AxisTickOpts(is_show=False),
                splitline_opts=opts.SplitLineOpts(is_show=False),
                axislabel_opts=opts.LabelOpts(is_show=False),
                split_number=20,
                min_="dataMin",
                max_="dataMax",
            ),
            yaxis_opts=opts.AxisOpts(
                grid_index=1,
                is_scale=True,
                split_number=2,
                axislabel_opts=opts.LabelOpts(is_show=False),
                axisline_opts=opts.AxisLineOpts(is_show=True),
                axistick_opts=opts.AxisTickOpts(is_show=True),
                splitline_opts=opts.SplitLineOpts(is_show=True),
            ),
            legend_opts=opts.LegendOpts(is_show=False),
        )
    )
    return bar

def my_strategy(data):
    x1=data.close>data.up
    x2=data.close.shift(1)<data.up.shift(1)
    x=x1&x2
    y1=data.close<data.down
    y2=data.close.shift(1)>data.down.shift(1)
    y=y1&y2
    data.loc[x,'signal']='buy'
    data.loc[y,'signal']='sell'
    buy_date=(data[data.signal=='buy'].index).strftime('%Y%m%d')
    sell_date=(data[data.signal=='sell'].index).strftime('%Y%m%d')
    buy_close=data[data.signal=='buy'].close.round(2).tolist()
    sell_close=data[data.signal=='sell'].close.round(2).tolist()
    return (buy_date,buy_close,sell_date,sell_close)

def get_sar (df, ty):
    t_color = "#f09320"
    if ty == 'up':
        t_color="#1ac6bc"
        
    esSar = (
    Scatter()
    .add_xaxis( df.trade_date.tolist())
    .add_yaxis(
        "sar", df.sar.to_numpy().round(2).tolist(),
        symbol_size = 5,
        label_opts=opts.LabelOpts(is_show=False),
        itemstyle_opts=opts.ItemStyleOpts(color=t_color),
    )
    .set_global_opts(xaxis_opts=opts.AxisOpts(type_="category"))
#     .set_global_opts(title_opts=opts.TitleOpts(title="EffectScatter-基本示例"))
    )
    return esSar

def get_stop_price_chart (df):
    t_color = "#0bcf3d"
    esSar = (
        Scatter()
        .add_xaxis( df.trade_date.tolist())
        .add_yaxis(
        "stop_price", df['stop_price'].to_numpy().round(2).tolist(),
        symbol_size = 5,
        label_opts=opts.LabelOpts(is_show=False),
        itemstyle_opts=opts.ItemStyleOpts(color=t_color),
    )
    .set_global_opts(xaxis_opts=opts.AxisOpts(type_="category"))
#     .set_global_opts(title_opts=opts.TitleOpts(title="EffectScatter-基本示例"))
    )
    return esSar

def get_bs (df, ty):
    t_color = "#0c9bdf"
    symbol=SymbolType.TRIANGLE
    if ty == 'buy':
        t_color="#f20d68"
        symbol=SymbolType.ROUND_RECT
        
    esSar = (
    EffectScatter()
    .add_xaxis( df.trade_date.tolist())
    .add_yaxis(
        ty, df['unit_price'].to_numpy().round(2).tolist(),
        symbol_size =10,
        label_opts=opts.LabelOpts(is_show=False),
        itemstyle_opts=opts.ItemStyleOpts(color=t_color),
        symbol=symbol
    )
    .set_global_opts(xaxis_opts=opts.AxisOpts(type_="category"))
#     .set_global_opts(title_opts=opts.TitleOpts(title="EffectScatter-基本示例"))
    )
    return esSar
    
def get_grid(stock_info,xdatas,kdatas,linetec_dic,vols,sar=None,bs=None, df_stop_price=None):
    kline = get_kline(xdatas, kdatas,stock_info)
    line = get_line(xdatas, linetec_dic)
    bar = get_volome(xdatas, vols, kdatas)

    if sar is not None:
        sar_up = get_sar(sar['up'],'up');
        kline.overlap(sar_up)
        
        sar_down = get_sar(sar['down'],'down');
        kline.overlap(sar_down)
    
    if bs is not None:
        bs_b = get_bs(bs['buy'],'buy')
        kline.overlap(bs_b)
        bs_s = get_bs(bs['sell'],'sell')
        kline.overlap(bs_s)
        
    if df_stop_price is not None:
        stop_p = get_stop_price_chart(df_stop_price)
        kline.overlap(stop_p)
    
    overlap_kline_line = kline.overlap(line)
    grid_chart = Grid(
        init_opts=opts.InitOpts(
            width="900px",
            height="800px",
        )
    )
    grid_chart.add(
        overlap_kline_line,
        grid_opts=opts.GridOpts(pos_left="6%", pos_right="8%", height="55%"),
    )
    
    grid_chart.add(
        bar,
        grid_opts=opts.GridOpts(
            pos_left="6%", pos_right="8%", pos_top="65%", height="10%"
        ),
    )
    
    return grid_chart

def get_macd_chart(xdatas,dif,dem,ocr):
    
    line= Line()
    line.add_xaxis(xaxis_data=xdatas)
    line.add_yaxis(
        series_name='dif',
        y_axis=dif,
        symbol="none",
        is_smooth=True,
        is_hover_animation=False,
        linestyle_opts=opts.LineStyleOpts(width=2, opacity=0.9),
        label_opts=opts.LabelOpts(is_show=False),
        itemstyle_opts=opts.ItemStyleOpts(color=g_colors[0]),
    )
    line.add_yaxis(
        series_name='dem',
        y_axis=dem,
        symbol="none",
        is_smooth=True,
        is_hover_animation=False,
        linestyle_opts=opts.LineStyleOpts(width=2, opacity=0.9),
        label_opts=opts.LabelOpts(is_show=False),
        itemstyle_opts=opts.ItemStyleOpts(color=g_colors[1]),
    )
    line.set_global_opts(xaxis_opts=opts.AxisOpts(type_="category"))
    bar = (
        Bar()
        .add_xaxis(xaxis_data=xdatas)
        .add_yaxis(
            series_name="ocr",
            yaxis_data=[
                [i, ocr[i],1 if ocr[i] >0 else -1]
                for i in range(len(ocr))
            ],
    #         yaxis_data = vols,
            xaxis_index=1,
            yaxis_index=1,
            label_opts=opts.LabelOpts(is_show=False)
        )
        .set_global_opts(
            title_opts=opts.TitleOpts(
                title='MACD',
                title_textstyle_opts = opts.TextStyleOpts(font_size=10),
                pos_top="75%",
            ),
            xaxis_opts=opts.AxisOpts(
                type_="category",
                is_scale=True,
                grid_index=2,
                boundary_gap=False,
#                 axisline_opts=opts.AxisLineOpts(is_on_zero=False),
#                 axistick_opts=opts.AxisTickOpts(is_show=False),
#                 splitline_opts=opts.SplitLineOpts(is_show=False),
#                 axislabel_opts=opts.LabelOpts(is_show=False),
                split_number=20,
#                 min_="dataMin",
#                 max_="dataMax",
            ),
            yaxis_opts=opts.AxisOpts(
                grid_index=2,
                is_scale=True,
                split_number=2,
#                 axislabel_opts=opts.LabelOpts(is_show=False),
#                 axisline_opts=opts.AxisLineOpts(is_show=False),
#                 axistick_opts=opts.AxisTickOpts(is_show=False),
#                 splitline_opts=opts.SplitLineOpts(is_show=False),
            ),
            legend_opts=opts.LegendOpts(is_show=False),
        )
    )
    bar.overlap(line)
    return bar

def get_dma_chart(xdatas,ddd,ama):
    line= Line()
    line.add_xaxis(xaxis_data=xdatas)
    line.add_yaxis(
        series_name='ddd',
        y_axis=ddd,
        symbol="none",
        is_smooth=True,
        is_hover_animation=False,
        linestyle_opts=opts.LineStyleOpts(width=2, opacity=0.9),
        label_opts=opts.LabelOpts(is_show=False),
        itemstyle_opts=opts.ItemStyleOpts(color=g_colors[0]),
    )
    line.add_yaxis(
        series_name='ama',
        y_axis=ama,
        symbol="none",
        is_smooth=True,
        is_hover_animation=False,
        linestyle_opts=opts.LineStyleOpts(width=2, opacity=0.9),
        label_opts=opts.LabelOpts(is_show=False),
        itemstyle_opts=opts.ItemStyleOpts(color=g_colors[1]),
    )
    line.set_global_opts(xaxis_opts=opts.AxisOpts(type_="category"))
    return line

/Users/david/anaconda3/lib/python3.6/site-packages/tushare/util/upass.py:28: FutureWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#ix-indexer-is-deprecated
  return str(df.ix[0]['token'])


In [2]:

sma_periods = [8,17,25,99,145]
stock_name = '上证综指'
hs,stockInfo = get_daily_data(stock_name,'20160101','')
hs = hs[['trade_date','close','open','high','low','vol']]

v1=np.array(hs.loc[:,['open','close','low','high']])
trade_dates = np.array(hs.trade_date)
vols = np.array(hs['vol'])
hs['sar'] = talib.SAR(hs.high, hs.low, acceleration=0.02, maximum=0.2)



#最近N1个交易日最高价
hs['up']=talib.MAX(hs.high,timeperiod=20).shift(1)
#最近N2个交易日最低价
hs['down']=talib.MIN(hs.low,timeperiod=10).shift(1)
#每日真实波动幅度
hs['ATR']=talib.ATR(hs.high,hs.low,hs.close,timeperiod=8)
tul_dic={}
tul_dic['upLine'] = {
    'name':'上轨道线',
    'datas': np.array(hs['up']).round(1).tolist()
}
tul_dic['downLine'] = {
    'name':'下轨道线',
    'datas': np.array(hs['down']).round(1).tolist()    
}

sma_dic= {}
for period in sma_periods:
    name = "SMA" + str(period)
    sma = talib.SMA(np.array(hs.close),period)
    sma_dic[name]={}
    sma_dic[name]['name'] = name;
    sma_dic[name]['datas'] = sma.round(2).tolist();

# sma_dic['sar'] = {}
# sma_dic['sar']['name'] = 'SAR'
# sma_dic['sar']['datas'] =  np.array(sar).round(2).tolist();
sar = {}
sar['down'] = hs.loc[hs['close'] > hs['sar'],['trade_date','sar']]
sar['up'] = (hs[hs['close'] < hs['sar']])[['trade_date','sar']]

grid_chart = get_grid(stockInfo,trade_dates.tolist(),v1.tolist(),sma_dic,vols.tolist(), sar=sar)
    
hs['macd_dif'],hs['macd_dem'],hs['macd_ocr'] = talib.MACD(hs.close,12,26,9)

macd = get_macd_chart(
    trade_dates.tolist(),
    hs.macd_dif.to_numpy().round(2).tolist(),
    hs.macd_dem.to_numpy().round(2).tolist(),
    (hs["macd_ocr"]*2).to_numpy().round(2).tolist()
)

grid_chart.add(
    macd,
    grid_opts=opts.GridOpts(
        pos_left="6%", pos_right="8%", pos_top="75%", height="10%"
    ),
)
grid_chart.render_notebook()

In [26]:
# sma_periods = [8,17,25,99,145,453 ]
sma_periods = [8,17,25,99]
stock_name = '京东方A'
start_day='20170101'
hs,stockInfo=get_daily_data(stock_name,start_day,'')
hs=hs[['trade_date','close','open','high','low','vol']]
v1=np.array(hs.loc[:,['open','close','low','high']])
trade_dates = np.array(hs.trade_date)
vols = np.array(hs['vol'])
hs['sar'] = talib.SAR(hs.high, hs.low, acceleration=0.1, maximum=2)



#最近N1个交易日最高价
hs['up']=talib.MAX(hs.high,timeperiod=20).shift(1)
#最近N2个交易日最低价
hs['down']=talib.MIN(hs.low,timeperiod=10).shift(1)
#每日真实波动幅度
hs['ATR']=talib.ATR(hs.high,hs.low,hs.close,timeperiod=25)
tul_dic={}
tul_dic['upLine'] = {
    'name':'上轨道线',
    'datas': np.array(hs['up']).round(1).tolist()
}
tul_dic['downLine'] = {
    'name':'下轨道线',
    'datas': np.array(hs['down']).round(1).tolist()    
}

sma_dic= {}
for period in sma_periods:
    name = "SMA" + str(period)
    sma = talib.SMA(np.array(hs.close),period)
    hs[name] =sma;
    sma_dic[name]={}
    sma_dic[name]['name'] = name;
    sma_dic[name]['datas'] = sma.round(2).tolist();
    
# for period in sma_periods:
#     name = "EMA" + str(period)
#     sma = talib.EMA(np.array(hs.close),period)
#     sma_dic[name]={}
#     sma_dic[name]['name'] = name;
#     sma_dic[name]['datas'] = sma.round(2).tolist();

# sma_dic['sar'] = {}
# sma_dic['sar']['name'] = 'SAR'
# sma_dic['sar']['datas'] =  np.array(sar).round(2).tolist();
sar = {}
sar['down'] = hs.loc[hs['close'] > hs['sar'],['trade_date','sar']]
sar['up'] = (hs[hs['close'] < hs['sar']])[['trade_date','sar']]


hs

pro.daily ts_code000725.SZ20170101


trade_date   close    open    high     low         vol       sar  \
trade_date                                                                    
2017-01-03   20170103  3.0050  2.7723  3.0534  2.7723  9914155.61       NaN   
2017-01-04   20170104  3.0243  2.9856  3.0437  2.9565  5289603.85  2.772300   
2017-01-05   20170105  2.9856  3.0147  3.0728  2.9662  4048673.44  2.799440   
2017-01-06   20170106  2.9953  2.9759  3.0340  2.9759  2856866.03  2.854112   
2017-01-09   20170109  3.0631  3.0050  3.0728  2.9953  4345830.03  2.897850   
...               ...     ...     ...     ...     ...         ...       ...   
2019-09-20   20190920  3.9400  3.9400  3.9700  3.9000  4674507.42  3.979560   
2019-09-23   20190923  3.9000  3.9200  3.9400  3.8700  3887609.53  3.970000   
2019-09-24   20190924  3.9000  3.9000  3.9500  3.8900  4153125.27  3.970000   
2019-09-25   20190925  3.7700  3.8700  3.8800  3.7600  7275235.63  3.950000   
2019-09-26   20190926  3.7100  3.7800  3.7900  3.7100  4124926.27  3.950000   

              up  down       ATR     SMA8     SMA17   SMA25     SMA99  
trade_date                                                             
2017-01-03   NaN   NaN       NaN      NaN       NaN     NaN       NaN  
2017-01-04   NaN   NaN       NaN      NaN       NaN     NaN       NaN  
2017-01-05   NaN   NaN       NaN      NaN       NaN     NaN       NaN  
2017-01-06   NaN   NaN       NaN      NaN       NaN     NaN       NaN  
2017-01-09   NaN   NaN       NaN      NaN       NaN     NaN       NaN  
...          ...   ...       ...      ...       ...     ...       ...  
2019-09-20  4.18  3.75  0.120668  3.97625  3.883529  3.8888  3.692182  
2019-09-23  4.18  3.83  0.118642  3.96250  3.890588  3.8920  3.695526  
2019-09-24  4.18  3.86  0.116296  3.94375  3.901176  3.8908  3.701675  
2019-09-25  4.18  3.86  0.117244  3.91125  3.907647  3.8856  3.705909  
2019-09-26  4.18  3.76  0.115754  3.87125  3.907059  3.8792  3.708836  

[668 rows x 14 columns]

## MACD

In [27]:
grid_chart = get_grid(stockInfo,trade_dates.tolist(),v1.tolist(),sma_dic,vols.tolist(), sar=sar)
    
hs['macd_dif'],hs['macd_dem'],hs['macd_ocr'] = talib.MACD(hs.close,12,26,9)

macd = get_macd_chart(
    trade_dates.tolist(),
    hs.macd_dif.to_numpy().round(2).tolist(),
    hs.macd_dem.to_numpy().round(2).tolist(),
    (hs["macd_ocr"]*2).to_numpy().round(2).tolist()
)

grid_chart.add(
    macd,
    grid_opts=opts.GridOpts(
        pos_left="6%", pos_right="8%", pos_top="75%", height="10%"
    ),
)
grid_chart.render_notebook()

## DMA

In [28]:
# grid_chart = get_grid(stockInfo,trade_dates.tolist(),v1.tolist(),sma_dic,vols.tolist(), sar)
    
# hs['DDD']= talib.SMA(np.array(hs.close),10) -  talib.SMA(np.array(hs.close),50)
# hs['AMA'] = talib.SMA(np.array(hs['DDD']),10)
# dma_chart = get_dma_chart(
#     trade_dates.tolist(),
#     hs['DDD'].to_numpy().round(2).tolist(),
#     hs['AMA'].to_numpy().round(2).tolist(),
# )
# grid_chart.add(
#     dma_chart,
#     grid_opts=opts.GridOpts(
#         pos_left="6%", pos_right="8%", pos_top="75%", height="10%"
#     ),
# )
# grid_chart.render_notebook()

In [29]:
def get_signal_sar ( df , start_date ):
    cond0 = df['trade_date'] > start_date
    
    cond1 = pd.notna(df['sar'].shift(1)) & pd.notna(df['ATR'])
    
    
    buy_cond1 = df['close'].shift(1) < df['sar'].shift(1) 
    #当日最高值突破前日sar
    buy_cond2 = (df['high'] > df['sar'].shift(1) )
    
    buy_cond3 = df['low'] > df['sar'].shift(1)
    
    df.loc[cond0&cond1& (buy_cond1&buy_cond2 | buy_cond3),'signal']='buy'
    
    sell_cond1 = df['close'].shift(1) > df['sar'].shift(1)
    sell_cond2 = df['low'] < df['sar'].shift(1)
    sell_cond3 = ( df['low'].shift(1) <  df['sar'].shift(2) ) & ( df['close'].shift(1) < df['sar'].shift(1) ) 
    df.loc[cond0&cond1& ( sell_cond1&sell_cond2 | sell_cond3 ),'signal']='sell'
    return df 

def get_signal_ema ( df , start_date ):
    cond0 = df['trade_date'] > start_date
    
    cond1 = pd.notna(df['sar'].shift(1)) & pd.notna(df['ATR'])
    
    
    buy_cond1 = df['close'].shift(1) < df['sar'].shift(1) 
    #当日最高值突破前日sar
    buy_cond2 = (df['high'] > df['sar'].shift(1) )
    
    buy_cond3 = df['low'] > df['sar'].shift(1)
    
    df.loc[cond0&cond1& (buy_cond1&buy_cond2 | buy_cond3),'signal']='buy'
    
    sell_cond1 = df['close'].shift(1) > df['sar'].shift(1)
    sell_cond2 = df['low'] < df['sar'].shift(1)
    sell_cond3 = ( df['low'].shift(1) <  df['sar'].shift(2) ) & ( df['close'].shift(1) < df['sar'].shift(1) ) 
    sell_cond4 = df['EMA8'] < df['EMA17']
    
    df.loc[cond0&cond1& ( sell_cond1&sell_cond2 | sell_cond3 ) & sell_cond4 ,'signal']='sell'
    return df 


def determind_buy_unit(df,initAmount):
    x = df['signal'] == 'buy'
    df.loc[ x,'unit'] =  100000/100/df['ATR']/df['sar']/100 * 10
    df.loc[:,'unit']=df['unit'].apply(np.ceil)
    return df

def stragyty_calc_buy( prev,cur,init_account,stop_atr_factor, account_risk):
    signal=None
    unit=unit_price=unit_cost=stop_price=R = None
    add = False
    add_price = 0
    
#     cond1 = prev['close'] < prev['sar'] and cur['close'] > cur['sar']
    sma_f = 'SMA17'
    sma_s = 'SMA25'
    cond2 = cur[sma_f] > cur[sma_s] and cur[sma_f] > prev[sma_f] and cur[sma_s] > prev[sma_s]
    cond1 = cur['unit_account'] == 0 and cur['close'] > cur['sar']
    
    add_cond1 = prev['unit_account'] > 0 and prev['add_price'] < cur['high'] and prev['add_price']>0
    if cond1 and prev['unit_account'] == 0 :
        signal = 'pre_buy'
    
    if prev['signal'] == 'pre_buy':         
        signal = 'buy'
#         unit =  np.ceil(init_account/100/prev['ATR']/prev['close']/100 * 1) * 100
        #以开盘价买入
        unit_price = cur['open']
            
    elif add_cond1 and cond2:
        signal='buy'
        add = True
        if cur['add_price'] < cur['low']:
            unit_price = cur['open']
        else:
            unit_price = prev['add_price']
        
        stop_price = unit_price - stop_atr_factor * cur['ATR']
        R = unit_price - stop_price
        unit = np.round ( init_account * account_risk / R / 100 ) * 100
        
        if np.floor( (unit+prev['unit_account'])/unit ) > 4:
            signal = None
            unit=0;
            unit_price =0;
            unit_cost = 0;
            stop_price = None
            add_price = 0;
        if signal == 'buy' and prev['account'] < unit_price * unit:
            signal = None
            unit=0;
            unit_price =0;
            unit_cost = 0;
            stop_price = None
            add_price = 0;
            
     
    if signal == 'buy':
        stop_price = unit_price - stop_atr_factor * cur['ATR']
        R = unit_price - stop_price
        unit = np.round ( init_account * account_risk / R / 100 ) * 100
        
        unit_cost = ( prev['unit_account'] * prev['unit_cost'] + unit_price * unit ) / (unit+prev['unit_account']) 
        add_price = unit_price + 0.5 * prev['ATR']
    

    return (signal,unit,unit_price,unit_cost,stop_price,R,add_price,add)

def stragyty_calc_sell( prev,cur):
    signal=None
    unit=unit_price = None
    if prev['unit_account'] > 0:
#         stop_price = prev['stop_price'] if prev['stop_price'] > prev['sar_stop_price'] else prev['sar_stop_price']
#         if stop_price > prev['close']:
        stop_price = prev['stop_price']
        #铁定要卖出
        if stop_price > prev['close']:
            a=1
#             signal = 'sell'
#             unit = 0 - prev['unit_account']
#             unit_price =cur['open']
            
        elif cur['low'] < stop_price:
            signal = 'sell'
            unit = 0 - prev['unit_account']
            
            unit_price = stop_price
    
    return (signal,unit,unit_price)

def stragyty_calc_pr(prev,cur):
    PdR=P=R=unit_cost =None
    
    if cur['unit_account'] > 0:
        unit_cost = cur['unit_cost']
        if unit_cost == 0:
            unit_cost = prev['unit_cost']
            
        R = cur['R']
        if R == 0:
            R = prev['R']        
        P = cur['close'] - unit_cost
        PdR = P / R
    else:
        if cur['signal'] == 'sell': 
            unit_cost = prev['unit_cost']
            R = prev['R']            
            P = cur['unit_price'] - unit_cost
            PdR = P / R
    return (unit_cost,R,P,PdR)

def is_exec_stragyty(prev,cur,start_date,end_date=''):    
    if pd.isna(prev['ATR']):
        return False
    
    if cur['trade_date'] < start_date:
        return False
    
    if end_date != '' and cur['trade_date'] > end_date:
        return False
    return True
    
def stragyty_calc(x,start_date,end_date,init_account,stop_atr_factor,account_risk):
    # 入市指标
    global g_prev_val 
    if g_prev_val is  None:
        g_prev_val = x.copy()
        return x 
    if  g_prev_val['trade_date'] == x['trade_date']:
        g_prev_val = x.copy()
        return x
    
    if is_exec_stragyty(g_prev_val,x,start_date, end_date) == False : 
        x['account'] = g_prev_val['account']
        x['balance'] = g_prev_val['balance']
        g_prev_val = x.copy()
        return x
    
    # print("====== trade_date:" + x['trade_date'])
    #入市
    signal,unit,unit_price,unit_cost,stop_price,R,add_price,add = stragyty_calc_buy( g_prev_val , x, init_account, stop_atr_factor , account_risk)
    if signal is not None: 
        x['signal'] = signal
    if signal == 'buy':
        x['signal'] = signal
        x['unit'] = unit
        x['unit_price']=unit_price
        x['unit_cost'] = unit_cost
        x['stop_price'] = stop_price
        x['R'] = R 
        
    x['add_price'] = add_price
    if x['add_price'] == 0:
        x['add_price'] = g_prev_val['add_price'] 
    
    signal,unit,unit_price = stragyty_calc_sell(g_prev_val, x)

    if signal == 'sell':
        x['signal'] = signal
        x['unit'] = unit
        x['unit_price'] = unit_price
        x['add_price'] = 0

 
    x['unit_account'] = g_prev_val['unit_account'] + x['unit']

    unit_cost,R,P,PdR = stragyty_calc_pr(g_prev_val,x)
    if unit_cost is not None:
        x['unit_cost'] = unit_cost
        x['R'] = R
        x['P/R'] = PdR
    
    if x['unit_account'] > 0:
        if g_prev_val['unit_account'] > 0:
            x['unit_high'] = x['high']  if x['high'] > g_prev_val['unit_high'] else g_prev_val['unit_high']
        else:
            x['unit_high'] = x['high']
    else:
        x['unit_high'] = 0
    
    if x['signal'] != "buy" or add:        
        x['stop_price'] = x['unit_high'] - x['ATR'] * stop_atr_factor
        x['stop_price']
    
    x['account'] = g_prev_val['account'] - x['unit'] * x['unit_price']
    x['unit_value'] = x['unit_account'] * x['close']
    x['balance'] = x['unit_value'] + x['account']

    g_prev_val = x.copy()
    return x
       

def get_line_ba(df,init_account) -> Line:
    trade_dates = np.array(df.trade_date).tolist()
    balances =np.array( (df['balance'] - init_account) / init_account).tolist()
    c = (
        Line()
        .add_xaxis(trade_dates)
        .add_yaxis("p"
                  , balances
                  , is_smooth=True,
                    is_hover_animation=False,
            linestyle_opts=opts.LineStyleOpts(width=2, opacity=0.9),
            label_opts=opts.LabelOpts(is_show=False),
                  )
        .set_global_opts(
            title_opts=opts.TitleOpts(title="Line-基本示例"),
             xaxis_opts=opts.AxisOpts(
                        is_scale=True,
                        type_="category",
                        splitarea_opts=opts.SplitAreaOpts(
                        is_show=True, areastyle_opts=opts.AreaStyleOpts(opacity=1)
                    ),
            ),
            yaxis_opts=opts.AxisOpts(
                    is_scale=True,
                    splitarea_opts=opts.SplitAreaOpts(
                        is_show=True, areastyle_opts=opts.AreaStyleOpts(opacity=1)
                    ),
            ),
            datazoom_opts=[
                opts.DataZoomOpts(
                    is_show=True,
                    xaxis_index=[0],
                    type_="slider",
                    pos_top="90%",
                    range_start=90,
                    range_end=100,
                ),
#                 opts.DataZoomOpts(
#                     is_show=True,
#                     yaxis_index=[0],
#                     type_="slider",
#                     orient = 'vertical',
# #                     pos_top="90%",
#                     pos_right="0%",
#                     range_start=0,
#                     range_end=100,
#                 ),
            ],
            tooltip_opts=opts.TooltipOpts(
                    trigger="axis",
                    axis_pointer_type="cross",
                    background_color="rgba(245, 245, 245, 0.8)",
                    border_width=1,
                    border_color="#ccc",
                    textstyle_opts=opts.TextStyleOpts(color="#000"),
            ),
        )
    )
    return c


In [30]:
ana_start_day ='20180101'
ana_end_day = ''    



hs['sar_stop_price'] = talib.SAR(hs.high, hs.low, acceleration=0.02, maximum=0.2)
sar_slow = {}
sar_slow['down'] = hs.loc[hs['close'] > hs['sar_stop_price'],['trade_date','sar_stop_price']]
sar_slow['up'] = (hs[hs['close'] < hs['sar_stop_price']])[['trade_date','sar_stop_price']]
sar_slow['up'].columns = ['trade_date','sar']
sar_slow['down'].columns = ['trade_date','sar']

g_prev_val = None
g_apply_flg = False
g_init_account = 100000.0
df1=hs.loc[:,['trade_date','open','close','high','low','sar','sar_stop_price','ATR','SMA8','SMA17','SMA25']]
rowCount = np.size( np.array(df1.index),0)
#init account
df1.loc[:, 'signal'] = np.array([''] * len(df1))
df1.loc[:, 'account'] = np.array([float(0)] * len(df1))
df1.loc[:, 'balance'] = np.array([float(g_init_account)] * len(df1))
df1.at[df1.index[0], 'account'] = g_init_account
#init unit
df1.loc[:, 'unit'] = np.array([float(0)] * len(df1))
df1.loc[:, 'unit_price'] = np.array([float(0)] * len(df1))
df1.loc[:, 'unit_account']  = np.array([float(0)] * len(df1))
df1.loc[:,'unit_value'] = np.array([float(0)] * len(df1))
df1.loc[:,'unit_high'] = np.array([float(0)] * len(df1))
df1.loc[:,'stop_price'] = np.array([float(0)] * len(df1))
df1.loc[:,'unit_cost'] =  np.array([float(0)] * len(df1))
df1.loc[:,'R'] = np.array([float(0)] * len(df1))
df1.loc[:,'P/R'] =  np.array([float(0)] * len(df1))
df1.loc[:,'add_price'] =  np.array([float(0)] * len(df1))
# get_signal_ema(df1,'20180101')


account_risk = 0.01

t=df1.apply(stragyty_calc,axis=1,args = ( ana_start_day,ana_end_day,g_init_account,2.5, account_risk))

bs = {}
bs['buy'] = t.loc[t['signal']=='buy',['trade_date','unit_price']]
bs['sell'] = t.loc[t['signal'] == 'sell', ['trade_date','unit_price']]


df_stop_price = t.loc[t['unit_account']>0,['trade_date','stop_price']]

if ana_end_day == '':
    t_disp = t.loc[ana_start_day:]
else:
    t_disp = t.loc[ana_start_day:ana_end_day]
c=get_line_ba(t_disp,g_init_account)
c.render_notebook()


In [31]:
if ana_end_day == '':
    dump_df = t.loc[ana_start_day:]
else:
    dump_df = t.loc[ana_start_day : ana_end_day]
dump_df.to_excel("output.xlsx",sheet_name='Sheet_name_1')

In [21]:
t.min()

trade_date         20160104
open                 7.5778
close                7.5306
high                  7.696
low                  7.4203
sar                  7.4203
sar_stop_price       7.4203
ATR               0.0721327
SMA8                7.77376
SMA17               7.82294
SMA25               7.85257
signal                     
account             31258.1
balance             93228.9
unit                  -6400
unit_price                0
unit_account              0
unit_value                0
unit_high                 0
stop_price         -1.33953
unit_cost                 0
R                         0
P/R                -0.97913
add_price                 0
dtype: object

In [22]:
t.max()

trade_date        20190926
open                 15.86
close                15.75
high                 16.04
low                  15.66
sar                  15.22
sar_stop_price       15.22
ATR               0.535811
SMA8               15.1063
SMA17              14.8182
SMA25              14.6576
signal                sell
account             110265
balance             114098
unit                  1600
unit_price           15.47
unit_account          6400
unit_value         82839.7
unit_high            16.04
stop_price         15.1249
unit_cost            15.04
R                  1.26446
P/R                 4.8527
add_price          15.6462
dtype: object

In [23]:
grid_chart = get_grid(
    stockInfo,
    trade_dates.tolist(),
    v1.tolist(),
    sma_dic,
    vols.tolist(),
    bs=bs,
    df_stop_price=df_stop_price,
    sar=sar_slow
)
hs['macd_dif'],hs['macd_dem'],hs['macd_ocr'] = talib.MACD(hs.close,12,26,9)

macd = get_macd_chart(
    trade_dates.tolist(),
    hs.macd_dif.to_numpy().round(2).tolist(),
    hs.macd_dem.to_numpy().round(2).tolist(),
    (hs["macd_ocr"]*2).to_numpy().round(2).tolist()
)

grid_chart.add(
    macd,
    grid_opts=opts.GridOpts(
        pos_left="6%", pos_right="8%", pos_top="75%", height="10%"
    ),
)
grid_chart.render_notebook()

In [12]:
t.loc['2019-02-25':'2019-02-26'][['ATR','open']]

ATR     open
trade_date                   
2019-02-25  0.310059  11.5780
2019-02-26  0.314285  12.4192

In [13]:
t.tail(20)[['signal','unit_price','unit_account','unit_cost','add_price','stop_price']]

signal  unit_price  unit_account  unit_cost  add_price  \
trade_date                                                            
2019-08-29                 0.00           0.0   0.000000   0.000000   
2019-08-30  pre_buy        0.00           0.0   0.000000   0.000000   
2019-09-02      buy       14.15        1100.0  14.150000  14.336916   
2019-09-03                 0.00        1100.0  14.150000  14.336916   
2019-09-04                 0.00        1100.0  14.150000  14.336916   
2019-09-05                 0.00        1100.0  14.150000  14.336916   
2019-09-06                 0.00        1100.0  14.150000  14.336916   
2019-09-09                 0.00        1100.0  14.150000  14.336916   
2019-09-10                 0.00        1100.0  14.150000  14.336916   
2019-09-11                 0.00        1100.0  14.150000  14.336916   
2019-09-12                 0.00        1100.0  14.150000  14.336916   
2019-09-16                 0.00        1100.0  14.150000  14.336916   
2019-09-17                 0.00        1100.0  14.150000  14.336916   
2019-09-18                 0.00        1100.0  14.150000  14.336916   
2019-09-19                 0.00        1100.0  14.150000  14.336916   
2019-09-20                 0.00        1100.0  14.150000  14.336916   
2019-09-23      buy       15.34        2200.0  14.745000  15.517534   
2019-09-24      buy       15.47        3300.0  14.986667  15.646233   
2019-09-25      buy       15.20        4400.0  15.040000  15.376383   
2019-09-26      buy       15.86        5500.0  15.204000  16.042728   

            stop_price  
trade_date              
2019-08-29   -0.943314  
2019-08-30   -0.934581  
2019-09-02   13.213802  
2019-09-03   13.585250  
2019-09-04   13.602240  
2019-09-05   13.937550  
2019-09-06   13.951048  
2019-09-09   14.097006  
2019-09-10   14.105126  
2019-09-11   14.115921  
2019-09-12   14.126284  
2019-09-16   14.129233  
2019-09-17   14.137063  
2019-09-18   14.147581  
2019-09-19   14.133678  
2019-09-20   14.512331  
2019-09-23   14.588837  
2019-09-24   14.658084  
2019-09-25   14.936361  
2019-09-26   15.124906

In [14]:
x = t['signal'] == 'sell' 
y = t['signal'] == 'buy'
t[x&y]

Empty DataFrame
Columns: [trade_date, open, close, high, low, sar, sar_stop_price, ATR, SMA8, SMA17, SMA25, signal, account, balance, unit, unit_price, unit_account, unit_value, unit_high, stop_price, unit_cost, R, P/R, add_price]
Index: []

[0 rows x 24 columns]

In [15]:
 ts.pro_bar(ts_code='000001.SZ', adj='qfq', start_date='20180101', end_date='20181011')

ts_code trade_date     open     high      low    close  pre_close  \
0    000001.SZ   20181011  10.0500  10.1600   9.7000   9.8600    10.4500   
1    000001.SZ   20181010  10.5400  10.6600  10.3800  10.4500    10.5600   
2    000001.SZ   20181009  10.4600  10.7000  10.3900  10.5600    10.4500   
3    000001.SZ   20181008  10.7000  10.7900  10.4500  10.4500    11.0500   
4    000001.SZ   20180928  10.7800  11.2700  10.7800  11.0500    10.7400   
..         ...        ...      ...      ...      ...      ...        ...   
182  000001.SZ   20180108  13.0388  13.0782  12.6550  12.7534    13.0880   
183  000001.SZ   20180105  12.9994  13.1372  12.9404  13.0880    13.0388   
184  000001.SZ   20180104  13.1077  13.1569  12.9207  13.0388    13.1175   
185  000001.SZ   20180103  13.5111  13.6391  12.9896  13.1175    13.4816   
186  000001.SZ   20180102  13.1372  13.7080  13.1077  13.4816    13.0880   

     change  pct_chg         vol       amount  
0   -0.5900  -5.6459  1995143.83  1994186.611  
1   -0.1100  -1.0417   995200.08  1045666.180  
2    0.1100   1.0526  1064084.26  1117946.550  
3   -0.6000  -5.4299  1686358.52  1793455.283  
4    0.3100   2.8864  2110242.67  2331358.288  
..      ...      ...         ...          ...  
182 -0.3346  -2.5565  2158620.81  2806099.169  
183  0.0492   0.3773  1210312.72  1603289.517  
184 -0.0787  -0.6000  1854509.48  2454543.516  
185 -0.3641  -2.7007  2962498.38  4006220.766  
186  0.3936   3.0073  2081592.55  2856543.822  

[187 rows x 11 columns]

In [16]:
a = 1 if 1 > 0.5 else 0.5

In [17]:
a

1